In [ ]:
%pip install -q -U distilabel "farm-haystack[preprocessing]"
%pip install -q -U "distilabel[hf-inference-endpoints, argilla]"
%pip install -q -U ollama openai

In [ ]:
import os
from typing import Dict

from distilabel.llm import OllamaLLM
from distilabel.pipeline import Pipeline, pipeline
from distilabel.tasks import TextGenerationTask, SelfInstructTask, Prompt

from datasets import Dataset
from haystack.nodes import PDFToTextConverter, PreProcessor

In [11]:
os.environ['OPENAI_API_KEY'] = "YOUR_TOKEN_MIGHT_GO_HERE"

In [ ]:
class QuestionAnsweringTask(TextGenerationTask):
    def generate_prompt(self, question: str) -> str:
        return Prompt(
            system_prompt=self.system_prompt,
            formatted_prompt=question,
        ).format_as(
            "openai"
        )  # type: ignore

    def parse_output(self, output: str) -> Dict[str, str]:
        return {"answer": output.strip()}

    @property
    def input_args_names(self) -> list[str]:
        return ["question"]

    @property
    def output_args_names(self) -> list[str]:
        return ["answer"]

In [ ]:
from distilabel.llm import OllamaLLM

llm = OllamaLLM(
    model="mixtral",  # should be deployed via `ollama notus:7b-v1-q5_K_M`
    task=QuestionAnsweringTask(),
    prompt_format="openai",
)

In [ ]:
generation = llm.generate(
    [{"question": "What's the second most populated city in Denmark?"}]
)

generation[0][0]["parsed_output"]["answer"]

In [ ]:
!zenml integration install s3 -y

In [ ]:
from zenml.client import Client

artifact = Client().get_artifact_version('86ba966e-66d1-4c79-a464-8bfff65300a0')
loaded_artifact = artifact.load()

In [ ]:
preprocessor = PreProcessor(
    clean_empty_lines=True,
    clean_whitespace=True,
    clean_header_footer=True,
    split_by="word",
    split_length=150,
    split_respect_sentence_boundary=True,
)
raw_texts = [{"content": doc.page_content} for doc in loaded_artifact]
docs = preprocessor.process(raw_texts)

In [ ]:
inputs = [doc.content for doc in docs]
inputs[0][0:500]

In [ ]:
instructions_dataset = Dataset.from_dict({"input": inputs})

instructions_dataset

In [ ]:
instructions_task = SelfInstructTask(
    application_description="An assistant that can answer questions about the open-source MLOps framework ZenML."
)

In [ ]:
instructions_generator = OllamaLLM(
    model="mixtral",
    task=instructions_task,
)

instructions_pipeline = Pipeline(generator=instructions_generator)

In [ ]:
generated_instructions = instructions_pipeline.generate(
    dataset=instructions_dataset, num_generations=1, batch_size=3
)

In [ ]:
instructions = []
for generations in generated_instructions["instructions"]:
    for generation in generations:
        instructions.extend(generation)

print(f"Number of generated instructions: {len(instructions)}")

for instruction in instructions[:5]:
    print(instruction)

In [ ]:
generated_instructions[0]

In [ ]:
instructions_rag_dataset = generated_instructions.to_argilla()
instructions_rag_dataset[0]

In [4]:
import argilla as rg
from argilla._constants import DEFAULT_API_KEY

# Argilla credentials
api_url = "https://strickvl-argilla.hf.space" # "https://<YOUR-HF-SPACE>.hf.space"
api_key = "admin.apikey"
# # Huggingface credentials
# hf_token = "hf_..."

rg.init(api_url=api_url, api_key=api_key)

# # If you want to use your private HF Space
# rg.init(extra_headers={"Authorization": f"Bearer {hf_token}"})

/home/strickvl/.pyenv/versions/3.10.12/envs/datagen/lib/python3.10/site-packages/argilla/client/client.py:178: UserWarning: No workspace configuration was detected. To work with Argilla datasets, specify a valid workspace name on `rg.init` or set it up through the `rg.set_workspace` function.
  warnings.warn(


In [ ]:
instructions_rag_dataset.push_to_argilla(name=f"ollama_instructions_zenml_rag", workspace="admin")

In [5]:
from distilabel.tasks import TextGenerationTask, UltraFeedbackTask

preference_pipeline = pipeline(
    "preference",
    "instruction-following",
    generator=OllamaLLM(
        model="mixtral",
        task=TextGenerationTask(),
        max_new_tokens=256,
        num_threads=2,
        temperature=0.3,
    ),
    labeller=OllamaLLM(
        model="mixtral",
        task=UltraFeedbackTask.for_instruction_following(),
        max_new_tokens=256,
        num_threads=2,
        temperature=0.3,
    ),
    max_new_tokens=256,
    num_threads=2,
    # api_key=os.getenv("OPENAI_API_KEY", None),
    temperature=0.0,
)

In [6]:
remote_dataset = rg.FeedbackDataset.from_argilla(
    "ollama_instructions_zenml_rag", workspace="admin"
)
instructions_dataset = remote_dataset.pull()

instructions_dataset = instructions_dataset.format_as("datasets")
instructions_dataset

Dataset({
    features: ['input', 'instructions', 'instruction-rating', 'instruction-rating-suggestion', 'instruction-rating-suggestion-metadata', 'external_id', 'metadata', 'vectors'],
    num_rows: 6154
})

In [7]:
instructions_dataset[0]

{'input': 'An end-to-end project\n\nPut your new knowledge in action with an end-to-end project\n\nThat was awesome! We learned so many advanced MLOps production concepts:\n\nThe value of deploying ZenML\u200b\n\nAbstracting infrastructure configuration into stacks\u200b\n\n\u200bConnecting remote storage\u200b\n\n\u200bOrchestrating on the cloud\u200b\n\n\u200bConfiguring the pipeline to scale compute\u200b\n\n\u200bConnecting a git repository\u200b\n\nWe will now combine all of these concepts into an end-to-end MLOps project powered by ZenML.\n\nGet started\n\nStart with a fresh virtual environment with no dependencies. Then let\'s install our dependencies:\n\npip install "zenml[templates,server]" notebook\n\nzenml integration install sklearn -y\n\nWe will then use\n\nZenML templates\n\nto help us get the code we need for the project:\n\nmkdir zenml_batch_e2e\n\ncd zenml_batch_e2e\n\nzenml init --template e2e_batch --template-with-defaults\n\n# Just in case, we install the requiremen

In [8]:
instructions_dataset = instructions_dataset.rename_columns({"input": "context", "instructions": "input"})

In [9]:
preference_dataset = preference_pipeline.generate(
    instructions_dataset,  # type: ignore
    num_generations=2,
    batch_size=8,
    display_progress_bar=True,
)

19:52:24 INFO     [PID: 14784] Executing dry-run...                                                 ]8;id=235490;file:///home/strickvl/.pyenv/versions/3.10.12/envs/datagen/lib/python3.10/site-packages/distilabel/pipeline.py\pipeline.py]8;;\:]8;id=199279;file:///home/strickvl/.pyenv/versions/3.10.12/envs/datagen/lib/python3.10/site-packages/distilabel/pipeline.py#747\747]8;;\

/home/strickvl/.pyenv/versions/3.10.12/envs/datagen/lib/python3.10/site-packages/distilabel/pipeline.py:680: UserWarning: Provided `num_generations=1` which implies that the `generator` LLM will just run once, while the `labelling` LLM expects to receive a list of N inputs to label, where N is > 1. If this is not intended, make sure to set `num_generations` to a value higher or equal to 2.
  return self._generate(


         INFO     [PID: 14784] Processing batch 1 of 1...                                           ]8;id=758540;file:///home/strickvl/.pyenv/versions/3.10.12/envs/datagen/lib/python3.10/site-packages/distilabel/pipeline.py\pipeline.py]8;;\:]8;id=628720;file:///home/strickvl/.pyenv/versions/3.10.12/envs/datagen/lib/python3.10/site-packages/distilabel/pipeline.py#577\577]8;;\

         INFO     [PID: 14784] Calling generator for batch 1...                                     ]8;id=633740;file:///home/strickvl/.pyenv/versions/3.10.12/envs/datagen/lib/python3.10/site-packages/distilabel/pipeline.py\pipeline.py]8;;\:]8;id=282808;file:///home/strickvl/.pyenv/versions/3.10.12/envs/datagen/lib/python3.10/site-packages/distilabel/pipeline.py#581\581]8;;\

19:52:32 INFO     [PID: 14784] Calling labeller for batch 1...                                      ]8;id=758686;file:///home/strickvl/.pyenv/versions/3.10.12/envs/datagen/lib/python3.10/site-packages/distilabel/pipeline.py\pipeline.py]8;;\:]8;id=523446;file:///home/strickvl/.pyenv/versions/3.10.12/envs/datagen/lib/python3.10/site-packages/distilabel/pipeline.py#612\612]8;;\

...

23:39:53 ERROR    [PID: 14784] exception calling callback for <Future at 0x778ba1f22b90 state=finished ]8;id=598654;file:///home/strickvl/.pyenv/versions/3.10.12/lib/python3.10/concurrent/futures/_base.py\_base.py]8;;\:]8;id=18078;file:///home/strickvl/.pyenv/versions/3.10.12/lib/python3.10/concurrent/futures/_base.py#344\344]8;;\
                  raised ReadError>                                                                                
                  ╭─────────────────────── Traceback (most recent call last) ────────────────────────╮             
                  │ /home/strickvl/.pyenv/versions/3.10.12/envs/datagen/lib/python3.10/site-packages │             
                  │ /httpx/_transports/default.py:66 in map_httpcore_exceptions                      │             
                  │                                                                                  │             
                  │    63 @contextlib.contextmanager                                                 │             
                  │    64 def map_httpcore_exceptions() -> typing.Iterator[None]:                    │             
                  │    65 │   try:                                                                   │             
                  │ ❱  66 │   │   yield                                                              │             
                  │    67 │   except Exception as exc:                                               │             
                  │    68 │   │   mapped_exc = None                                                  │             
                  │    69                                                                            │             
                  │                                                                                  │             
                  │ ╭────────────────────── locals ───────────────────────╮                          │             
                  │ │   from_exc = <class 'httpcore.RemoteProtocolError'> │                          │             
                  │ │ mapped_exc = <class 'httpx.ReadError'>              │                          │             
                  │ │    message = '[Errno 104] Connection reset by peer' │                          │             
                  │ │     to_exc = <class 'httpx.RemoteProtocolError'>    │                          │             
                  │ ╰─────────────────────────────────────────────────────╯                          │             
                  │                                                                                  │             
                  │ /home/strickvl/.pyenv/versions/3.10.12/envs/datagen/lib/python3.10/site-packages │             
                  │ /httpx/_transports/default.py:228 in handle_request                              │             
                  │                                                                                  │             
                  │   225 │   │   │   extensions=request.extensions,                                 │             
                  │   226 │   │   )                                                                  │             
                  │   227 │   │   with map_httpcore_exceptions():                                    │             
                  │ ❱ 228 │   │   │   resp = self._pool.handle_request(req)                          │             
                  │   229 │   │                                                                      │             
                  │   230 │   │   assert isinstance(resp.stream, typing.Iterable)                    │             
                  │   231                                                                            │             
                  │                                                                                  │             
                  │ ╭──────────────────────────── locals ──────

         ERROR    [PID: 14784] exception calling callback for <Future at 0x778ba1f20b50 state=finished ]8;id=70035;file:///home/strickvl/.pyenv/versions/3.10.12/lib/python3.10/concurrent/futures/_base.py\_base.py]8;;\:]8;id=121689;file:///home/strickvl/.pyenv/versions/3.10.12/lib/python3.10/concurrent/futures/_base.py#344\344]8;;\
                  raised RemoteProtocolError>                                                                      
                  ╭─────────────────────── Traceback (most recent call last) ────────────────────────╮             
                  │ /home/strickvl/.pyenv/versions/3.10.12/envs/datagen/lib/python3.10/site-packages │             
                  │ /httpx/_transports/default.py:66 in map_httpcore_exceptions                      │             
                  │                                                                                  │             
                  │    63 @contextlib.contextmanager                                                 │             
                  │    64 def map_httpcore_exceptions() -> typing.Iterator[None]:                    │             
                  │    65 │   try:                                                                   │             
                  │ ❱  66 │   │   yield                                                              │             
                  │    67 │   except Exception as exc:                                               │             
                  │    68 │   │   mapped_exc = None                                                  │             
                  │    69                                                                            │             
                  │                                                                                  │             
                  │ ╭──────────────────────────── locals ────────────────────────────╮               │             
                  │ │   from_exc = <class 'httpcore.RemoteProtocolError'>            │               │             
                  │ │ mapped_exc = <class 'httpx.RemoteProtocolError'>               │               │             
                  │ │    message = 'Server disconnected without sending a response.' │               │             
                  │ │     to_exc = <class 'httpx.RemoteProtocolError'>               │               │             
                  │ ╰────────────────────────────────────────────────────────────────╯               │             
                  │                                                                                  │             
                  │ /home/strickvl/.pyenv/versions/3.10.12/envs/datagen/lib/python3.10/site-packages │             
                  │ /httpx/_transports/default.py:228 in handle_request                              │             
                  │                                                                                  │             
                  │   225 │   │   │   extensions=request.extensions,                                 │             
                  │   226 │   │   )                                                                  │             
                  │   227 │   │   with map_httpcore_exceptions():                                    │             
                  │ ❱ 228 │   │   │   resp = self._pool.handle_request(req)                          │             
                  │   229 │   │                                                                      │             
                  │   230 │   │   assert isinstance(resp.stream, typing.Iterable)                    │             
                  │   231                                                                            │             
                  │                                                                                  │             
                  │ ╭──────────────────────────── locals ──────

23:39:54 ERROR    [PID: 14784] exception calling callback for <Future at 0x778ba1f20640 state=finished ]8;id=955659;file:///home/strickvl/.pyenv/versions/3.10.12/lib/python3.10/concurrent/futures/_base.py\_base.py]8;;\:]8;id=455505;file:///home/strickvl/.pyenv/versions/3.10.12/lib/python3.10/concurrent/futures/_base.py#344\344]8;;\
                  raised ConnectError>                                                                             
                  ╭─────────────────────── Traceback (most recent call last) ────────────────────────╮             
                  │ /home/strickvl/.pyenv/versions/3.10.12/envs/datagen/lib/python3.10/site-packages │             
                  │ /httpx/_transports/default.py:66 in map_httpcore_exceptions                      │             
                  │                                                                                  │             
                  │    63 @contextlib.contextmanager                                                 │             
                  │    64 def map_httpcore_exceptions() -> typing.Iterator[None]:                    │             
                  │    65 │   try:                                                                   │             
                  │ ❱  66 │   │   yield                                                              │             
                  │    67 │   except Exception as exc:                                               │             
                  │    68 │   │   mapped_exc = None                                                  │             
                  │    69                                                                            │             
                  │                                                                                  │             
                  │ ╭────────────────────── locals ───────────────────────╮                          │             
                  │ │   from_exc = <class 'httpcore.RemoteProtocolError'> │                          │             
                  │ │ mapped_exc = <class 'httpx.ConnectError'>           │                          │             
                  │ │    message = '[Errno 111] Connection refused'       │                          │             
                  │ │     to_exc = <class 'httpx.RemoteProtocolError'>    │                          │             
                  │ ╰─────────────────────────────────────────────────────╯                          │             
                  │                                                                                  │             
                  │ /home/strickvl/.pyenv/versions/3.10.12/envs/datagen/lib/python3.10/site-packages │             
                  │ /httpx/_transports/default.py:228 in handle_request                              │             
                  │                                                                                  │             
                  │   225 │   │   │   extensions=request.extensions,                                 │             
                  │   226 │   │   )                                                                  │             
                  │   227 │   │   with map_httpcore_exceptions():                                    │             
                  │ ❱ 228 │   │   │   resp = self._pool.handle_request(req)                          │             
                  │   229 │   │                                                                      │             
                  │   230 │   │   assert isinstance(resp.stream, typing.Iterable)                    │             
                  │   231                                                                            │             
                  │                                                                                  │             
                  │ ╭──────────────────────────── locals ─────

23:39:55 ERROR    [PID: 14784] exception calling callback for <Future at 0x778ba1f23c40 state=finished ]8;id=872537;file:///home/strickvl/.pyenv/versions/3.10.12/lib/python3.10/concurrent/futures/_base.py\_base.py]8;;\:]8;id=754074;file:///home/strickvl/.pyenv/versions/3.10.12/lib/python3.10/concurrent/futures/_base.py#344\344]8;;\
                  raised ConnectError>                                                                             
                  ╭─────────────────────── Traceback (most recent call last) ────────────────────────╮             
                  │ /home/strickvl/.pyenv/versions/3.10.12/envs/datagen/lib/python3.10/site-packages │             
                  │ /httpx/_transports/default.py:66 in map_httpcore_exceptions                      │             
                  │                                                                                  │             
                  │    63 @contextlib.contextmanager                                                 │             
                  │    64 def map_httpcore_exceptions() -> typing.Iterator[None]:                    │             
                  │    65 │   try:                                                                   │             
                  │ ❱  66 │   │   yield                                                              │             
                  │    67 │   except Exception as exc:                                               │             
                  │    68 │   │   mapped_exc = None                                                  │             
                  │    69                                                                            │             
                  │                                                                                  │             
                  │ ╭────────────────────── locals ───────────────────────╮                          │             
                  │ │   from_exc = <class 'httpcore.RemoteProtocolError'> │                          │             
                  │ │ mapped_exc = <class 'httpx.ConnectError'>           │                          │             
                  │ │    message = '[Errno 111] Connection refused'       │                          │             
                  │ │     to_exc = <class 'httpx.RemoteProtocolError'>    │                          │             
                  │ ╰─────────────────────────────────────────────────────╯                          │             
                  │                                                                                  │             
                  │ /home/strickvl/.pyenv/versions/3.10.12/envs/datagen/lib/python3.10/site-packages │             
                  │ /httpx/_transports/default.py:228 in handle_request                              │             
                  │                                                                                  │             
                  │   225 │   │   │   extensions=request.extensions,                                 │             
                  │   226 │   │   )                                                                  │             
                  │   227 │   │   with map_httpcore_exceptions():                                    │             
                  │ ❱ 228 │   │   │   resp = self._pool.handle_request(req)                          │             
                  │   229 │   │                                                                      │             
                  │   230 │   │   assert isinstance(resp.stream, typing.Iterable)                    │             
                  │   231                                                                            │             
                  │                                                                                  │             
                  │ ╭──────────────────────────── locals ─────

╭─────────────────────────────── Traceback (most recent call last) ────────────────────────────────╮
│ in <module>:1                                                                                    │
│                                                                                                  │
│ ❱ 1 preference_dataset = preference_pipeline.generate(                                           │
│   2 │   instructions_dataset,  # type: ignore                                                    │
│   3 │   num_generations=2,                                                                       │
│   4 │   batch_size=8,                                                                            │
│                                                                                                  │
│ /home/strickvl/.pyenv/versions/3.10.12/envs/datagen/lib/python3.10/site-packages/distilabel/pipe │
│ line.py:753 in generate                                                                          │
│                                                                                                  │
│   750 │   │   │   │   "Dry-run executed with no issues. Starting the actual generation..."       │
│   751 │   │   │   )                                                                              │
│   752 │   │                                                                                      │
│ ❱ 753 │   │   dataset = use_progress_bar(self._generate)(                                        │
│   754 │   │   │   dataset=dataset,                                                               │
│   755 │   │   │   num_generations=num_generations,                                               │
│   756 │   │   │   batch_size=batch_size,                                                         │
│                                                                                                  │
│ /home/strickvl/.pyenv/versions/3.10.12/envs/datagen/lib/python3.10/site-packages/distilabel/prog │
│ ress_bar.py:45 in wrapper                                                                        │
│                                                                                                  │
│    42 │   def wrapper(*args: P.args, **kwargs: P.kwargs) -> R:                                   │
│    43 │   │   _pipeline_progress.start()                                                         │
│    44 │   │   try:                                                                               │
│ ❱  45 │   │   │   r = func(*args, **kwargs)                                                      │
│    46 │   │   finally:                                                                           │
│    47 │   │   │   _pipeline_progress.stop()                                                      │
│    48 │   │   return r                                                                           │
│                                                                                                  │
│ /home/strickvl/.pyenv/versions/3.10.12/envs/datagen/lib/python3.10/site-packages/distilabel/pipe │
│ line.py:614 in _generate                                                                         │
│                                                                                                  │
│   611 │   │   │   if self.labeller is not None:                                                  │
│   612 │   │   │   │   logger.info(f"Calling labeller for batch {batch_i}...")                    │
│   613 │   │   │   │   try:                                                                       │
│ ❱ 614 │   │   │   │   │   batch_labels = self._get_batch_labels(                                 │
│   615 │   │   │   │   │   │   inputs=inputs,                                                     │
│   616 │   │   │   │   │   │   progress_callback_func=labelling_progress_func,                    │
│   617 │   │   │   │   │   │   batch_size=batch_size,       

In [10]:
preference_dataset[0]

╭─────────────────────────────── Traceback (most recent call last) ────────────────────────────────╮
│ in <module>:1                                                                                    │
│                                                                                                  │
│ ❱ 1 preference_dataset[0]                                                                        │
│   2                                                                                              │
╰──────────────────────────────────────────────────────────────────────────────────────────────────╯
NameError: name 'preference_dataset' is not defined

In [ ]:
# Uploading the Preference Dataset
preference_rg_dataset = preference_dataset.to_argilla()

# Adding the context as a metadata property in the new Feedback dataset, as this
# information will be useful later.
for record_feedback, record_huggingface in zip(
    preference_rg_dataset, preference_dataset
):
    record_feedback.metadata["context"] = record_huggingface["context"]

preference_rg_dataset.push_to_argilla(name=f"ollama_instructions_zenml_rag", workspace="admin")

In [ ]:
preference_rg_dataset.push_to_huggingface("strickvl/ollama_instructions_zenml_rag")